In [1]:
import pandas as pd
import os
import re
from tslearn.metrics import dtw, dtw_path
from tslearn.barycenters import dtw_barycenter_averaging

df_train = pd.read_pickle(os.path.join(r"data/df_train.pkl"))

df_test = pd.read_pickle(os.path.join(r"data/df_test.pkl"))

df_train = pd.concat([df_train,df_test], ignore_index=True)
print(df_train)
print(df_test)


d:\anaconda\envs\ml_mvp_1\lib\site-packages\tslearn\bases.py:15: UserWarning: h5py not installed, hdf5 features will not be supported.
Install h5py to use hdf5 features: http://docs.h5py.org/
  warn(h5py_msg)


                 Libelle Date et heure de comptage  Débit horaire  \
0      AV_Champs_Elysees       2019-11-01 04:00:00          746.0   
1      AV_Champs_Elysees       2019-11-01 05:00:00          549.0   
2      AV_Champs_Elysees       2019-11-01 06:00:00          503.0   
3      AV_Champs_Elysees       2019-11-01 07:00:00          500.0   
4      AV_Champs_Elysees       2019-11-01 08:00:00          525.0   
...                  ...                       ...            ...   
28500          Sts_Peres       2020-12-02 20:00:00          565.0   
28501          Sts_Peres       2020-12-02 21:00:00          422.0   
28502          Sts_Peres       2020-12-02 22:00:00          239.0   
28503          Sts_Peres       2020-12-02 23:00:00          142.0   
28504          Sts_Peres       2020-12-03 00:00:00          129.0   

       Taux d'occupation  Etat trafic  Etat arc            filename  \
0               10.98889            1  Invalide  champs-elysees.csv   
1                7.40722     

In [2]:
mapper = {'AV_Champs_Elysees': "0", 'Convention': "1", 'Sts_Peres': "2"}
df_train['Libelle'] = df_train['Libelle'].map(mapper)
df_test['Libelle'] = df_test['Libelle'].map(mapper)

mapper_2 = {'Invalide': "0", 'Barré': "1"}
df_train['Etat arc'] = df_train['Etat arc'].map(mapper_2)
df_test['Etat arc'] = df_test['Etat arc'].map(mapper_2)
print(df_train["Libelle"].unique())

print(df_train["precipMM"].unique())

['0' '1' '2']
[0.  1.2 1.6 0.8 2.7 3.6 1.8 1.3 0.9 0.1 0.2 0.7 1.  0.5 1.1 1.5 0.4 0.6
 0.3 2.1 1.4 1.7 2.  1.9 2.6 3.5 2.2 2.4 3.2 4.4 5.9 3.  2.8 4.2 2.9 2.5
 3.7 4.  3.8 2.3]


In [3]:
print(df_train.columns)
cat_columns = ["Etat trafic", "Etat arc", 'Jour de la semaine_0', 'Jour de la semaine_1', 'Jour de la semaine_2',
       'Jour de la semaine_3', 'Jour de la semaine_4', 'Jour de la semaine_5',
       'Jour de la semaine_6', 'Etat du confinement', 'Couvre-feu',
       'Jour férié', 'Vacances scolaires']
bool_columns = ['Couvre-feu',
       'Jour férié', 'Vacances scolaires']
object_columns = ["Etat arc"]
# df_meta_train = pd.DataFrame()
# #df_meta_train[cat_columns] = df_train[cat_columns].apply(lambda x: x.astype(pd.CategoricalDtype(categories=df_meta.index)).cat.codes)
# df_meta_train[cat_columns] = df_train[cat_columns]
# df_meta_train['Libelle'] = df_train["Libelle"].astype(str)
# df_meta_train.index = df_meta_train['Libelle']

# df_meta_test = pd.DataFrame()
# #df_meta_train[cat_columns] = df_train[cat_columns].apply(lambda x: x.astype(pd.CategoricalDtype(categories=df_meta.index)).cat.codes)
# df_meta_test[cat_columns] = df_test[cat_columns]
# df_meta_test['Libelle'] = df_test["Libelle"].astype(str)
# df_meta_test.index = df_meta_test['Libelle']

# print(df_meta_test.index)
# print(df_meta_train['Etat arc'].unique())


# cat_code = dict(enumerate(df_meta_train.index))
# cat_code_reverse = {v:k for k,v in cat_code.items()}

print(df_train.dtypes)

Index(['Libelle', 'Date et heure de comptage', 'Débit horaire',
       'Taux d'occupation', 'Etat trafic', 'Etat arc', 'filename', 'Date',
       'Jour de la semaine_0', 'Jour de la semaine_1', 'Jour de la semaine_2',
       'Jour de la semaine_3', 'Jour de la semaine_4', 'Jour de la semaine_5',
       'Jour de la semaine_6', 'Etat du confinement', 'Couvre-feu',
       'Jour férié', 'Vacances scolaires',
       'Date des prochaines vacances scolaires',
       'Temps avant les prochaines vacances scolaires', 'tempC',
       'windspeedKmph', 'winddirDegree', 'weatherCode', 'precipMM', 'humidity',
       'visibility', 'pressure', 'cloudcover', 'HeatIndexC', 'DewPointC',
       'WindChillC', 'WindGustKmph', 'FeelsLikeC', 'uvIndex', 'maxtempC',
       'mintempC', 'avgtempC', 'totalSnow_cm', 'sunHour', 'uvIndex', 'sunrise',
       'sunset', 'moon_phase', 'moon_illumination', 'Journée'],
      dtype='object')
Libelle                                                   object
Date et heure de co

In [4]:
def chunks(l, size, step):
    """ Yield successive n-sized chunks from l.
    """
    l = l[:(len(l) // size) * size]
    return [x for x in [l[i : i + size] for i in range(0, len(l), step)] if len(x) == size]

In [5]:
print(df_train["Libelle"])
print(df_test["Libelle"].unique())
print(df_train['Journée'])

0        0
1        0
2        0
3        0
4        0
        ..
28500    2
28501    2
28502    2
28503    2
28504    2
Name: Libelle, Length: 28505, dtype: object
['0' '1' '2']
0        False
1        False
2        False
3        False
4         True
         ...  
28500    False
28501    False
28502    False
28503    False
28504    False
Name: Journée, Length: 28505, dtype: bool


In [6]:
#paramètres
N_input = 14*24
N_output = 7*24
device = 'cuda'
p_test = 0.2
#meta_specs = {'cat_input_dim': (len(cat_columns), len(df_meta_train.index)),
#              'embed_dim': 8}
optimizer_parameters = {'lr': 0.001}
batch_size = 32

In [7]:
from sklearn.preprocessing import MinMaxScaler
#visibility 
metatemp_columns = cat_columns + ['windspeedKmph', 'weatherCode', 'precipMM', 'cloudcover', 'HeatIndexC', 'maxtempC', 'mintempC']
num_columns = ['windspeedKmph', 'weatherCode', 'precipMM', 'cloudcover', 'HeatIndexC', 'maxtempC', 'mintempC']
df_train[bool_columns] = df_train[bool_columns].apply(lambda x : x.astype(int))
#df_test[bool_columns] = df_test[bool_columns].apply(lambda x : x.astype(int))
df_train[object_columns] = df_train[object_columns].apply(lambda x : x.astype(int))
#df_test[object_columns] = df_test[object_columns].apply(lambda x : x.astype(int))
print(df_test)
#std_scaler = MinMaxScaler().fit(df_train[num_columns])
#df_std = std_scaler.transform(df_train[num_columns])
#print(df_std.head())
#print(df_train.dtypes)
metatemp_data_train = df_train.sort_values(['Date et heure de comptage', 'Libelle']).groupby('Libelle')[metatemp_columns].apply(lambda x: chunks(x.values, size=N_input+N_output, step=1))
#metatemp_data_test = df_test.sort_values(['Date et heure de comptage', 'Libelle']).groupby('Libelle')[metatemp_columns].apply(lambda x: chunks(x.values, size=N_input+N_output, step=1))

print(metatemp_data_train.head())
print(metatemp_data_train[0])
print(len(metatemp_data_train.values[0]))

      Libelle Date et heure de comptage  Débit horaire  Taux d'occupation  \
9259        0       2020-11-23 00:00:00           91.0            1.38722   
9260        0       2020-11-23 01:00:00           63.0            0.91056   
9261        0       2020-11-23 02:00:00           47.0            0.74278   
9262        0       2020-11-23 03:00:00           51.0            0.61056   
9263        0       2020-11-23 04:00:00           32.0            0.35334   
...       ...                       ...            ...                ...   
28500       2       2020-12-02 20:00:00          565.0            5.79944   
28501       2       2020-12-02 21:00:00          422.0            3.94778   
28502       2       2020-12-02 22:00:00          239.0            2.58000   
28503       2       2020-12-02 23:00:00          142.0            1.83667   
28504       2       2020-12-03 00:00:00          129.0            1.68500   

       Etat trafic Etat arc            filename        Date  \
9259        

In [8]:
import numpy as np
data_train = df_train.sort_values(['Date et heure de comptage', 'Libelle']).groupby('Libelle')['Débit horaire'].apply(lambda x: chunks(x.values, size=N_input+N_output, step=1))
#data_test = df_test.sort_values(['Date et heure de comptage', 'Libelle']).groupby('Libelle')['Débit horaire'].apply(lambda x: chunks(x.values, size=N_input+N_output, step=1))
#print(data_test.head())
# metadata_train =df_train.sort_values(['Date et heure de comptage', 'Libelle']).groupby('Libelle')['Débit horaire',"Taux d'occupation"].apply(lambda x: chunks(x.values, size=N_input+N_output, step=1))
# metadata_test = df_meta_test.sort_values(['Date et heure de comptage', 'Libelle']).groupby('Libelle')['Débit horaire',"Taux d'occupation"].apply(lambda x: chunks(x.values, size=N_input+N_output, step=1))

#print(data.values)
data_numpy_train = np.array([np.array(x) for x in data_train.values])
#data_numpy_test = np.array([np.array(x) for x in data_test.values])
metatemp_data_numpy_train = np.array([np.array(x) for x in metatemp_data_train.values])
#metatemp_data_numpy_test = np.array([np.array(x) for x in metatemp_data_test.values])
#data_numpy.astype(float)

print(metatemp_data_numpy_train[0][0][0])

rues = np.array([x for x in data_train.index])


# meta_cat_train = metadata_train[cat_columns].values.astype(int)
# meta_cat_train = np.array([np.array(x) for x in meta_cat_train.values])

# metadata_test = df_meta_test.loc[rues]
# meta_cat_test = metadata_test[cat_columns].values.astype(int)
# meta_cat_test = np.array([np.array(x) for x in meta_cat_test.values])
print(rues)

[  1.   0.   0.   0.   0.   0.   1.   0.   0.   0.   0.   1.   1.  11.
 143.   0.  79.  11.  16.   9.]
['0' '1' '2']


In [9]:
# Mélange les rues
print(len(data_numpy_train)==len(metatemp_data_numpy_train))
ind_train = np.arange(len(data_numpy_train))
np.random.shuffle(ind_train)
#ind_test = np.arange(len(data_numpy_test))
#np.random.shuffle(ind_test)
data_numpy = data_numpy_train[ind_train]
#data_numpy_test = data_numpy_test[ind_test]
# meta_cat_train = meta_cat_train[ind_train]
# meta_cat_test = meta_cat_test[ind_test]
metatemp_data_numpy = metatemp_data_numpy_train[ind_train]
#metatemp_data_numpy_test = metatemp_data_numpy_test[ind_test]
print(metatemp_data_numpy_train[0].shape)
print(data_numpy_train[0].shape)

metatemp_data_numpy_train = []
metatemp_data_numpy_test = []
data_numpy_test = []
data_numpy_train = []
#data_numpy_test = data_numpy[nb_train:]
#data_numpy_train = data_numpy[:nb_train]
print(len(data_numpy))
for i in range(len(metatemp_data_numpy)):
    nb_train = int(len(data_numpy[i])*(1-p_test))
    metatemp_data_numpy_train.append(metatemp_data_numpy[i][:nb_train])
    metatemp_data_numpy_test.append(metatemp_data_numpy[i][nb_train:])
    data_numpy_test.append(data_numpy[i][nb_train:])
    data_numpy_train.append(data_numpy[i][:nb_train])
print(metatemp_data_numpy_train[0].shape)
print(data_numpy_train[0].shape)
print(metatemp_data_numpy_train[0][0][0])

True
(8569, 504, 20)
(8569, 504)
3
(6855, 504, 20)
(6855, 504)
[  1.   0.   0.   0.   0.   0.   1.   0.   0.   0.   0.   1.   1.  11.
 143.   0.  79.  11.  16.   9.]


In [10]:
# Concatène chaque départements ensembles

# meta_cat_train = np.concatenate(meta_cat_train)
# meta_cat_test = np.concatenate(meta_cat_test)
data_numpy_train = np.concatenate(data_numpy_train)
data_numpy_test = np.concatenate(data_numpy_test)
metatemp_data_numpy_train = np.concatenate(metatemp_data_numpy_train)
metatemp_data_numpy_test = np.concatenate(metatemp_data_numpy_test)

data_numpy_train[data_numpy_train < 0] = 0
data_numpy_test[data_numpy_test < 0] = 0
print(metatemp_data_numpy_train.shape)
print(metatemp_data_numpy_train[0][0][13:])

(20565, 504, 20)
[ 11. 143.   0.  79.  11.  16.   9.]


In [11]:
# Normalise par mean-std calculées sur le data de train
std = data_numpy_train.std((0,1))[None]
mean = data_numpy_train.mean((0,1))[None]
meta_std = metatemp_data_numpy_train[:][:][13:].std((0,1))[None]
meta_mean = metatemp_data_numpy_train[:][:][13:].mean((0,1))[None]
print(meta_std[None][0][0])


data_numpy_train = (data_numpy_train-mean[None])/std[None]
#data_numpy_test = (data_numpy_test-mean[None])/std[None]
for i in range (len(metatemp_data_numpy_train)):
    for j in range (len(metatemp_data_numpy_train[i])):
        for k in range (len(num_columns)):
            metatemp_data_numpy_train[i][j][len(cat_columns)+k] = (metatemp_data_numpy_train[i][j][len(cat_columns)+k]-meta_mean[None][0][0][len(cat_columns)+k])/meta_std[None][0][0][len(cat_columns)+k]

# for i in range (len(metatemp_data_numpy_test)):
#     for j in range (len(metatemp_data_numpy_test[i])):
#         for k in range (len(num_columns)):
#             metatemp_data_numpy_test[i][j][len(cat_columns)+k] = (metatemp_data_numpy_test[i][j][len(cat_columns)+k]-meta_mean[None][0][0][len(cat_columns)+k])/meta_std[None][0][0][len(cat_columns)+k]
print(metatemp_data_numpy_train[0][0][13:])

def rescale(data):
    return data * std + mean

[5.66456121e-01 6.81511034e-02 3.50910504e-01 3.50910504e-01
 3.50910504e-01 3.47570519e-01 3.50910504e-01 3.47469854e-01
 3.50762281e-01 1.09837332e+00 0.00000000e+00 1.78994259e-01
 4.77125016e-01 6.65596853e+00 7.46845933e+01 2.89874209e-01
 3.48049858e+01 7.39364891e+00 7.93940205e+00 6.08825762e+00]
[-0.42861663 -0.18043344 -0.31614296  0.84948497 -0.4080233  -0.13440827
 -0.24998048]


In [12]:
# Sépare en input/output
X_train, y_train = data_numpy_train[:, :N_input], data_numpy_train[:, N_input:]
X_test, y_test = data_numpy_test[:, :N_input], data_numpy_test[:, N_input:]
print(metatemp_data_numpy_test)
X_meta_train, y_meta_train = metatemp_data_numpy_train[:, :N_input, :], metatemp_data_numpy_train[:, N_input:, :]
X_meta_test, y_meta_test = metatemp_data_numpy_test[:, :N_input, :], metatemp_data_numpy_test[:, N_input:, :]
X_train = X_train[:,:,None]
y_train = y_train[:,:,None]
X_test = X_test[:,:,None]
y_test = y_test[:,:,None]
print(X_train.shape)
print(X_meta_train.shape)

[[[ 1.  0.  0. ... 27. 26. 20.]
  [ 1.  0.  0. ... 27. 26. 20.]
  [ 1.  0.  0. ... 27. 26. 20.]
  ...
  [ 1.  0.  0. ... 27. 30. 19.]
  [ 1.  0.  0. ... 28. 30. 19.]
  [ 1.  0.  0. ... 29. 30. 19.]]

 [[ 1.  0.  0. ... 27. 26. 20.]
  [ 1.  0.  0. ... 27. 26. 20.]
  [ 1.  0.  0. ... 26. 26. 20.]
  ...
  [ 1.  0.  0. ... 28. 30. 19.]
  [ 1.  0.  0. ... 29. 30. 19.]
  [ 2.  0.  0. ... 28. 30. 19.]]

 [[ 1.  0.  0. ... 27. 26. 20.]
  [ 1.  0.  0. ... 26. 26. 20.]
  [ 1.  0.  0. ... 26. 26. 20.]
  ...
  [ 1.  0.  0. ... 29. 30. 19.]
  [ 2.  0.  0. ... 28. 30. 19.]
  [ 1.  0.  0. ... 28. 30. 19.]]

 ...

 [[ 1.  0.  0. ... 16. 15. 12.]
  [ 1.  0.  0. ... 15. 15. 12.]
  [ 1.  0.  0. ... 15. 15. 12.]
  ...
  [ 1.  0.  0. ... 14. 15. 11.]
  [ 1.  0.  0. ... 14. 15. 11.]
  [ 1.  0.  0. ... 14. 15. 11.]]

 [[ 1.  0.  0. ... 15. 15. 12.]
  [ 1.  0.  0. ... 15. 15. 12.]
  [ 1.  0.  0. ... 14. 15. 12.]
  ...
  [ 1.  0.  0. ... 14. 15. 11.]
  [ 1.  0.  0. ... 14. 15. 11.]
  [ 1.  0.  0. ... 14. 15. 1

In [13]:
# Install a pip package in the current Jupyter kernel
# import sys
# !{sys.executable} -m pip install torch===1.6.0 torchvision===0.7.0 -f https://download.pytorch.org/whl/torch_stable.html
import torch

#import torch

#print(type(X_train))
#print(data_numpy.dtype)
#print(torch.from_numpy(X_train))
#print(torch.from_numpy(y_train))
#print(torch.from_numpy(y_meta_train))

dataset_train = torch.utils.data.TensorDataset(torch.FloatTensor(X_train),
                                                torch.FloatTensor(X_meta_train),
                                               torch.FloatTensor(y_train),
                                              torch.FloatTensor(y_meta_train))
dataset_test = torch.utils.data.TensorDataset(torch.FloatTensor(X_test),
                                              torch.FloatTensor(X_meta_test),
                                              torch.FloatTensor(y_test),
                                             torch.FloatTensor(y_meta_test))


trainloader = torch.utils.data.DataLoader(
    dataset_train, batch_size=batch_size, shuffle=True, num_workers=1)
testloader = torch.utils.data.DataLoader(
    dataset_test, batch_size=batch_size, shuffle=False, num_workers=1)
for i, data in enumerate(trainloader, 0):
    inputs, metatemp_inputs, target, metatemp_target = data
    print(inputs)
    print(metatemp_inputs)

tensor([[[-0.9067],
         [-0.8796],
         [-0.7226],
         ...,
         [-0.4247],
         [-0.4328],
         [-0.5980]],

        [[-1.0610],
         [-1.0123],
         [-0.9798],
         ...,
         [-0.9798],
         [-0.8823],
         [-1.1314]],

        [[-1.0312],
         [-1.2343],
         [-1.3399],
         ...,
         [-0.2243],
         [-0.5384],
         [-0.8525]],

        ...,

        [[-0.0213],
         [-0.5087],
         [-0.6522],
         ...,
         [ 0.8181],
         [ 0.1710],
         [ 0.2170]],

        [[-1.3643],
         [-1.3886],
         [-1.3859],
         ...,
         [-0.6657],
         [-0.8958],
         [-1.0664]],

        [[ 0.0708],
         [ 0.1006],
         [ 0.1222],
         ...,
         [-1.2776],
         [-1.2451],
         [-1.2830]]])
tensor([[[ 1.0000,  0.0000,  0.0000,  ..., -0.8138, -0.8901, -0.4142],
         [ 1.0000,  0.0000,  0.0000,  ..., -0.8138, -0.8901, -0.4142],
         [ 1.0000,  0.0000, 

         [ 1.0000,  0.0000,  1.0000,  ...,  1.0797,  1.3770,  1.0640]]])
tensor([[[ 1.2134],
         [ 1.5573],
         [ 1.2838],
         ...,
         [ 0.8100],
         [ 1.0726],
         [ 1.3894]],

        [[ 0.9075],
         [ 0.8668],
         [-0.6649],
         ...,
         [-0.3056],
         [ 0.6069],
         [ 0.5934]],

        [[-1.3534],
         [-1.1125],
         [-0.8227],
         ...,
         [-0.7605],
         [-1.1504],
         [-1.2641]],

        ...,

        [[ 0.1818],
         [-0.2812],
         [-0.4707],
         ...,
         [-1.1910],
         [-0.7848],
         [ 0.1764]],

        [[ 0.7964],
         [ 0.3984],
         [ 0.7531],
         ...,
         [ 0.1818],
         [ 1.1051],
         [ 1.1918]],

        [[ 0.0545],
         [ 0.6502],
         [ 0.7504],
         ...,
         [-1.2533],
         [-1.1720],
         [-0.6440]]])
tensor([[[ 4.0000e+00,  0.0000e+00,  0.0000e+00,  ..., -6.7853e-01,
          -7.6418e-01, -4.142

tensor([[[-1.2099],
         [-0.9013],
         [-0.4058],
         ...,
         [-0.3137],
         [-0.2216],
         [-0.4301]],

        [[ 0.9833],
         [ 1.1836],
         [ 0.8993],
         ...,
         [ 0.8316],
         [ 0.6990],
         [ 0.7558]],

        [[-1.0664],
         [-1.0529],
         [-0.9635],
         ...,
         [-0.3679],
         [-0.2460],
         [-0.0321]],

        ...,

        [[-0.5439],
         [-0.7334],
         [-0.9852],
         ...,
         [ 0.3145],
         [ 0.3199],
         [ 0.3497]],

        [[ 1.3001],
         [ 1.3542],
         [ 1.6114],
         ...,
         [ 1.9364],
         [ 1.8849],
         [ 2.0176]],

        [[-0.2893],
         [-0.8011],
         [-1.1422],
         ...,
         [ 0.1060],
         [-0.3679],
         [-0.4112]]])
tensor([[[ 1.0000,  0.0000,  0.0000,  ...,  0.1330,  0.6213,  0.5713],
         [ 1.0000,  0.0000,  0.0000,  ...,  0.1330,  0.6213,  0.5713],
         [ 1.0000,  0.0000, 

         [ 0.3443]]])
tensor([[[ 2.0000,  0.0000,  0.0000,  ..., -0.6785, -0.7642, -1.0712],
         [ 2.0000,  0.0000,  0.0000,  ..., -0.6785, -0.7642, -1.0712],
         [ 1.0000,  0.0000,  0.0000,  ..., -0.6785, -0.7642, -1.0712],
         ...,
         [ 1.0000,  0.0000,  0.0000,  ..., -0.8138, -0.6382, -0.7427],
         [ 1.0000,  0.0000,  0.0000,  ..., -0.6785, -0.6382, -0.7427],
         [ 1.0000,  0.0000,  0.0000,  ..., -0.5433, -0.6382, -0.7427]],

        [[ 2.0000,  0.0000,  1.0000,  ..., -0.2728, -0.5123, -1.0712],
         [ 2.0000,  0.0000,  1.0000,  ..., -0.2728, -0.5123, -1.0712],
         [ 2.0000,  0.0000,  1.0000,  ..., -0.4080, -0.5123, -1.0712],
         ...,
         [ 2.0000,  0.0000,  1.0000,  ..., -0.4080, -0.6382, -0.4142],
         [ 2.0000,  0.0000,  1.0000,  ..., -0.2728, -0.6382, -0.4142],
         [ 2.0000,  0.0000,  1.0000,  ..., -0.4080, -0.6382, -0.4142]],

        [[ 2.0000,  0.0000,  0.0000,  ..., -1.3548, -1.5199, -2.2210],
         [ 1.0000,  0.0

         [ 1.0000,  0.0000,  0.0000,  ..., -0.5433, -0.7642, -0.2500]]])
tensor([[[-0.6874],
         [ 0.1249],
         [ 0.6096],
         ...,
         [-1.0664],
         [-1.1395],
         [-1.0366]],

        [[-0.7659],
         [-0.7226],
         [-0.9798],
         ...,
         [ 0.4174],
         [ 0.1872],
         [ 0.1574]],

        [[ 0.7315],
         [ 0.7721],
         [ 0.9129],
         ...,
         [-1.0014],
         [-0.5439],
         [-0.0808]],

        ...,

        [[-0.2893],
         [-0.3922],
         [-0.8254],
         ...,
         [ 0.1764],
         [-0.1296],
         [-0.4951]],

        [[-1.0908],
         [-1.2289],
         [-1.2885],
         ...,
         [-0.5411],
         [-0.7307],
         [-0.9717]],

        [[-0.2108],
         [-0.0077],
         [-0.1567],
         ...,
         [-0.6007],
         [-0.5276],
         [-0.2731]]])
tensor([[[ 1.0000,  0.0000,  0.0000,  ...,  0.1330,  0.3694,  0.7355],
         [ 1.0000,  0.0000

...

         [ 1.0000,  0.0000,  0.0000,  ..., -0.5433, -0.6382, -0.0857]]])
tensor([[[ 0.9345],
         [ 1.1674],
         [ 1.7685],
         ...,
         [-0.7036],
         [-0.6305],
         [-0.6955]],

        [[ 0.5880],
         [ 0.4228],
         [ 0.3957],
         ...,
         [-0.8471],
         [-0.1323],
         [ 0.4255]],

        [[-0.2514],
         [-0.4139],
         [-0.8850],
         ...,
         [-0.0348],
         [-0.3029],
         [-0.2271]],

        ...,

        [[ 1.2540],
         [ 0.5121],
         [ 0.2901],
         ...,
         [ 1.5898],
         [ 1.9364],
         [ 1.7414]],

        [[-1.0394],
         [-1.1747],
         [-1.2912],
         ...,
         [-0.7902],
         [-0.9554],
         [-0.8769]],

        [[-0.8282],
         [-0.9554],
         [-1.1774],
         ...,
         [ 0.5961],
         [ 0.0654],
         [-0.3651]]])
tensor([[[ 1.0000,  0.0000,  0.0000,  ..., -0.5433, -0.7642, -0.5785],
         [ 1.0000,  0.0000

         [ 1.0000,  0.0000,  0.0000,  ...,  1.3502,  0.7473,  1.2283]]])
tensor([[[-0.4978],
         [ 0.7477],
         [ 1.2649],
         ...,
         [-1.2018],
         [-1.1720],
         [-1.0637]],

        [[-0.4924],
         [-0.3679],
         [-0.7523],
         ...,
         [-1.3209],
         [-1.3616],
         [-1.3886]],

        [[ 0.9454],
         [ 0.6150],
         [ 0.2224],
         ...,
         [ 1.6791],
         [ 1.1132],
         [ 0.5094]],

        ...,

        [[-0.4437],
         [-0.5168],
         [-0.7442],
         ...,
         [-0.9148],
         [-0.8498],
         [-0.9852]],

        [[-0.3137],
         [-0.3543],
         [-0.1621],
         ...,
         [ 0.6286],
         [ 0.8614],
         [ 0.5419]],

        [[-1.1991],
         [-1.1422],
         [-1.0746],
         ...,
         [-1.3778],
         [-1.2993],
         [-1.2722]]])
tensor([[[ 1.0000e+00,  0.0000e+00,  0.0000e+00,  ..., -1.6253e+00,
          -1.2680e+00, -1.564

         [ 0.5744]]])
tensor([[[ 2.0000,  0.0000,  0.0000,  ..., -0.9490, -1.2680, -1.2355],
         [ 2.0000,  0.0000,  0.0000,  ..., -0.9490, -1.2680, -1.2355],
         [ 1.0000,  0.0000,  0.0000,  ..., -0.9490, -1.2680, -1.2355],
         ...,
         [ 1.0000,  0.0000,  0.0000,  ..., -1.0843, -1.3939, -1.2355],
         [ 1.0000,  0.0000,  0.0000,  ..., -1.0843, -1.3939, -1.2355],
         [ 2.0000,  0.0000,  0.0000,  ..., -1.0843, -1.3939, -1.2355]],

        [[ 1.0000,  0.0000,  0.0000,  ...,  0.6740,  0.7473,  1.2283],
         [ 1.0000,  0.0000,  0.0000,  ...,  0.8092,  0.7473,  1.2283],
         [ 1.0000,  0.0000,  0.0000,  ...,  0.8092,  0.7473,  1.2283],
         ...,
         [ 1.0000,  0.0000,  0.0000,  ...,  1.0797,  1.8809,  1.2283],
         [ 1.0000,  0.0000,  0.0000,  ...,  0.8092,  1.8809,  1.2283],
         [ 1.0000,  0.0000,  0.0000,  ...,  0.8092,  1.8809,  1.2283]],

        [[ 1.0000,  0.0000,  0.0000,  ..., -0.1375, -0.5123,  0.0785],
         [ 2.0000,  0.0

         [ 0.4553]]])
tensor([[[ 1.0000,  0.0000,  0.0000,  ..., -1.2195, -1.0161, -0.9070],
         [ 1.0000,  0.0000,  0.0000,  ..., -1.2195, -1.0161, -0.9070],
         [ 2.0000,  0.0000,  0.0000,  ..., -1.2195, -1.0161, -0.9070],
         ...,
         [ 1.0000,  0.0000,  0.0000,  ..., -1.4900, -1.1420, -1.3997],
         [ 1.0000,  0.0000,  0.0000,  ..., -1.4900, -1.1420, -1.3997],
         [ 1.0000,  0.0000,  0.0000,  ..., -1.4900, -1.1420, -1.3997]],

        [[ 2.0000,  0.0000,  0.0000,  ...,  1.0797,  0.6213,  0.4070],
         [ 1.0000,  0.0000,  0.0000,  ...,  0.9445,  0.6213,  0.4070],
         [ 2.0000,  0.0000,  0.0000,  ...,  0.9445,  0.6213,  0.4070],
         ...,
         [ 2.0000,  0.0000,  0.0000,  ...,  0.6740,  0.4954,  1.0640],
         [ 2.0000,  0.0000,  0.0000,  ...,  0.8092,  0.4954,  1.0640],
         [ 2.0000,  0.0000,  0.0000,  ...,  0.8092,  0.4954,  1.0640]],

        [[ 1.0000,  0.0000,  0.0000,  ..., -0.4080, -0.1344, -0.2500],
         [ 1.0000,  0.0

tensor([[[ 0.6990],
         [ 0.4201],
         [ 0.0275],
         ...,
         [-0.9798],
         [-0.0727],
         [ 0.9562]],

        [[ 0.2901],
         [ 0.1439],
         [-0.0375],
         ...,
         [ 1.7414],
         [ 1.3651],
         [ 0.7991]],

        [[-0.6901],
         [-0.9121],
         [-1.0854],
         ...,
         [-0.1485],
         [-0.2704],
         [-0.2487]],

        ...,

        [[ 0.4878],
         [ 0.2657],
         [ 0.4580],
         ...,
         [-0.6142],
         [-0.4762],
         [-0.1567]],

        [[-1.2776],
         [-1.3697],
         [-1.3751],
         ...,
         [-0.8715],
         [-1.1125],
         [-1.2289]],

        [[-1.1179],
         [-1.1368],
         [-1.2614],
         ...,
         [-0.7171],
         [-0.8958],
         [-0.9744]]])
tensor([[[ 1.0000,  0.0000,  0.0000,  ..., -0.4080, -0.2604, -0.0857],
         [ 1.0000,  0.0000,  0.0000,  ..., -0.4080, -0.2604, -0.0857],
         [ 1.0000,  0.0000, 

In [14]:
def fake_baye(outputs, log_sigmas, target):
    loss = 1/2 * (log_sigmas + torch.exp(-log_sigmas) * (outputs - target)**2)
    return loss.mean()

def loss_rescale_factor(log_rescale_factor, outputs, log_sigmas, target):
    batch_size = outputs.shape[0]
    loss = 1/2 * torch.exp(-2 * log_rescale_factor) * torch.sum(torch.exp(-log_sigmas) * (outputs - target)**2)
    loss += batch_size * log_rescale_factor
    return loss.sum()

In [15]:
import tqdm

def train_model(net, loss_type, optimizer_parameters, epochs=1000, gamma=0.001,
                eval_every=50, Lambda=1, alpha=0.5, beta=0.):
    optimizer = torch.optim.Adam(net.parameters(), **optimizer_parameters)
    criterion = torch.nn.MSELoss()

    if hasattr(net, 'log_rescale_factor'):
        optimizer_rescale_factor = torch.optim.Adam([net.log_rescale_factor], **optimizer_parameters)

    t = tqdm.notebook.tqdm(range(epochs))
    for epoch in t:
        for i, data in enumerate(trainloader, 0):

            net.train()
            if hasattr(net, 'log_rescale_factor'):
                net.log_rescale_factor.require_grad = False
            
            
            inputs, metatemp_inputs, target, metatemp_target = data
            inputs = inputs.to(device)
            metatemp_inputs = metatemp_inputs.to(device)
            target = target.to(device)
            metatemp_target = metatemp_target.to(device)
            batch_size, N_output = target.shape[0:2]
            #print(inputs)
            #print(metatemp_inputs)
            # forward + backward + optimize
            
            outputs = net(inputs, meta_temporal_input=metatemp_inputs, meta_temporal_target=metatemp_target)
            if len(outputs) == 2:
                outputs, _ = outputs
            else:
                outputs, log_sigmas, _ = outputs

            loss_mse, loss_shape, loss_temporal = torch.tensor(
                0), torch.tensor(0), torch.tensor(0)

            loss = 0
            if 'mse' in loss_type:
                loss_mse = 100 * criterion(outputs, target)
                loss += loss_mse

            if 'dilate' in loss_type:
                loss_dilate, loss_shape, loss_temporal = dilate_loss(
                    outputs, target, alpha, gamma, device)
                loss += loss_dilate

            if 'fake_baye' in loss_type:
                loss_fake_baye = fake_baye(outputs, log_sigmas, target)
                loss += loss_fake_baye

            if 'all_target_regression' in loss_type:
                loss_target_week_regression = F.mse_loss(outputs.sum(1), target.sum(1))
                loss += loss_target_week_regression

            optimizer.zero_grad()
            loss.backward()
            optimizer.step()

            if hasattr(net, 'log_rescale_factor'):
                net.log_rescale_factor.require_grad = True

                loss_rescale = loss_rescale_factor(net.log_rescale_factor, outputs.detach(), log_sigmas.detach(),
                                                   target)
                optimizer_rescale_factor.zero_grad()
                loss_rescale.backward()
                optimizer_rescale_factor.step()

        if (epoch % eval_every == 0):
            eval_mse, eval_dtw, eval_tdi = eval_model(net, testloader, gamma)

        t.set_postfix(loss=loss.item(),
                      loss_shape=loss_shape.item(),
                      loss_temporal=loss_temporal.item(),
                      mse=eval_mse,
                      dtw=eval_dtw,
                      tdi=eval_tdi)

In [16]:
def eval_model(net, loader, gamma):
    criterion = torch.nn.MSELoss()
    losses_mse = []
    losses_dtw = []
    losses_tdi = []

    net.eval()

    for i, data in enumerate(loader, 0):
        loss_mse, loss_dtw, loss_tdi = torch.tensor(
            0), torch.tensor(0), torch.tensor(0)
        # get the inputs
        inputs, metatemp_inputs, target, metatemp_target = data
        inputs = inputs.to(device)
        metatemp_inputs = metatemp_inputs.to(device)
        target = target.to(device)
        metatemp_target = metatemp_target.to(device)
        batch_size, N_output = target.shape[0:2]
        outputs = net(inputs, meta_temporal_input=metatemp_inputs, meta_temporal_target=metatemp_target)
        if len(outputs) == 2:
            outputs, _ = outputs
        else:
            outputs, prewarp_outputs, warp_matrix = outputs

        # MSE
        loss_mse = criterion(target, outputs)
        loss_dtw, loss_tdi = 0, 0
        # DTW and TDI
        for k in range(batch_size):
            target_k_cpu = target[k, :, 0:1].view(-1).detach().cpu().numpy()
            output_k_cpu = outputs[k, :, 0:1].view(-1).detach().cpu().numpy()

            loss_dtw += dtw(target_k_cpu, output_k_cpu)
            path, sim = dtw_path(target_k_cpu, output_k_cpu)

            Dist = 0
            for i, j in path:
                Dist += (i - j) * (i - j)
            loss_tdi += Dist / (N_output * N_output)

        loss_dtw = loss_dtw / batch_size
        loss_tdi = loss_tdi / batch_size

        # print statistics
        losses_mse.append(loss_mse.item())
        losses_dtw.append(loss_dtw)
        losses_tdi.append(loss_tdi)

    return np.array(losses_mse).mean(), np.array(losses_dtw).mean(), np.array(losses_tdi).mean()


In [17]:
import torch.nn as nn
import torch.nn.functional as F

class Encoder(nn.Module):
    def __init__(self, input_dim, enc_hid_dim, dec_hid_dim, num_layers, dropout):
        super().__init__()
        self.enc_hid_dim = enc_hid_dim
        self.num_layers = num_layers
      
        self.rnn = nn.GRU(input_dim, enc_hid_dim,
                          num_layers=num_layers,
                          bidirectional=True,
                          batch_first=True,
                          dropout=dropout)

        self.fc = nn.Linear(enc_hid_dim * 2, dec_hid_dim)

        self.dropout = nn.Dropout(dropout)

    def forward(self, src, meta_temporal, hidden=None):
       
        if meta_temporal is not None:
            src = torch.cat([src, meta_temporal], dim=2)
        
        

        outputs, hidden = self.rnn(src, hidden)

        # outputs = [batch size, src len, hid dim * num directions]
        # hidden = [n layers * num directions, batch size, hid dim]

        hidden = torch.cat((hidden[::2, :, :], hidden[1::2, :, :]), dim=2)
        hidden = self.dropout(hidden)
        hidden = torch.tanh(self.fc(hidden))

        # outputs = [batch size, src len, enc hid dim * 2]
        # hidden = [batch size, dec hid dim]

        return outputs, hidden


class Attention(nn.Module):
    def __init__(self, enc_hid_dim, dec_hid_dim):
        super().__init__()

        self.attn = nn.Linear((enc_hid_dim * 2) + dec_hid_dim, dec_hid_dim)
        self.v = nn.Linear(dec_hid_dim, 1, bias=False)

    def forward(self, hidden, encoder_outputs):

        # hidden = [batch size, dec hid dim]
        # encoder_outputs = [batch size, src len, enc hid dim * 2]

        src_len = encoder_outputs.shape[1]

        # repeat decoder hidden state src_len times
        hidden = hidden.unsqueeze(1).repeat(1, src_len, 1)

        # hidden = [batch size, src len, dec hid dim]
        # encoder_outputs = [batch size, src len, enc hid dim * 2]

        energy = torch.tanh(
            self.attn(torch.cat((hidden, encoder_outputs), dim=2)))

        # energy = [batch size, src len, dec hid dim]

        attention = self.v(energy).squeeze(2)

        # attention= [batch size, src len]

        return F.softmax(attention, dim=1)


class Decoder(nn.Module):
    def __init__(self, input_dim, output_dim, enc_hid_dim, dec_hid_dim, fc_dim,
                 num_layers, dropout, attention, meta_temporal_dim, bayesian=False, embed_dim=None):
        super().__init__()

        self.output_dim = output_dim
        self.attention = attention
        self.num_layers = num_layers
        self.enc_hid_dim = enc_hid_dim
        self.dec_hid_dim = dec_hid_dim
        self.fc_dim = fc_dim
        
        self.embed_dim = embed_dim if embed_dim is not None else 0
        self.meta_temporal_dim = meta_temporal_dim if meta_temporal_dim is not None else 0
        
        self.bayesian = bayesian
        
        if self.bayesian:
            self.out_log_sigma = nn.Linear(fc_dim + output_dim, output_dim)

            self.rnn = nn.GRU((enc_hid_dim * 2) + (input_dim * 2) + meta_temporal_dim,
                              dec_hid_dim,
                              num_layers=num_layers,
                              batch_first=True,
                              dropout=dropout)
            self.fc_1 = nn.Linear(
                (enc_hid_dim * 2) + dec_hid_dim + (input_dim * 2) + self.embed_dim, fc_dim)

        else:
            self.rnn = nn.GRU((enc_hid_dim * 2) + output_dim + meta_temporal_dim,
                              dec_hid_dim,
                              num_layers=num_layers,
                              batch_first=True,
                              dropout=dropout)

            self.fc_1 = nn.Linear(
                (enc_hid_dim * 2) + dec_hid_dim + output_dim + self.embed_dim, fc_dim)
        
        self.fc_2 = nn.Linear(fc_dim, fc_dim)
        self.out = nn.Linear(fc_dim, output_dim)

        self.dropout = nn.Dropout(dropout)

    def forward(self, inputs, hidden, encoder_outputs, meta_temporal, embeddings=None):

        a = self.attention(hidden[-1, :, :], encoder_outputs)

        # a = [batch size, src len]

        a = a.unsqueeze(1)

        # a = [batch size, 1, src len]

        weighted = torch.bmm(a, encoder_outputs)

        # weighted = [batch size, 1, enc hid dim * 2]

        if meta_temporal is not None:
            rnn_input = torch.cat((inputs, meta_temporal, weighted), dim=2)
        else:
            rnn_input = torch.cat((inputs, weighted), dim=2)

        # rnn_input = [batch size, 1, (enc hid dim * 2) + emb dim]

        output, hidden = self.rnn(rnn_input, hidden)

        # output = [batch size, seq len, dec hid dim * n directions]
        # hidden = [n layers * n directions, batch size, dec hid dim]

        hidden_prediction = torch.cat((output, weighted, inputs), dim=2)
        
        if embeddings is not None:
            hidden_prediction = torch.cat((hidden_prediction, embeddings), dim=2)
        
        #hidden_prediction = self.fc(hidden_prediction)
        hidden_prediction = self.fc_1(F.relu(hidden_prediction))
        hidden_prediction = self.fc_2(F.relu(hidden_prediction))

        prediction = self.out(F.relu(hidden_prediction))

        # prediction = [batch size, output dim]

        if not self.bayesian:
            return prediction, hidden
        else:
            log_sigma = self.out_log_sigma(torch.cat([hidden_prediction, prediction], dim=-1))
            return prediction, log_sigma, hidden


class MetaEmbedder(nn.Module):
    def __init__(self, cat_input_dim, num_input_dim, embed_dim):
        """cat_input_dim should be a tuple (nb_of_inputs, nb_of_categories)"""
        super().__init__()

        self.cat_input_dim = cat_input_dim
        self.num_input_dim = num_input_dim
        self.embed_dim = embed_dim
        # self.cat_module = nn.Embedding(cat_input_dim[1], embed_dim)
        self.num_module = nn.Linear(num_input_dim, embed_dim)
        #self.fc = nn.Linear(self.embed_dim * (cat_input_dim[0] + 1), self.enc_hid_dim * self.num_layers * 2)
        self.fc = nn.Linear(self.embed_dim, self.embed_dim)

    def forward(self, inputs_cat, inputs_num):
        batch_size = inputs_cat.shape[0]
        #x_cat = self.cat_module(inputs_cat).reshape(batch_size, -1)
        x_num = F.relu(self.num_module(inputs_num))
        #x = torch.cat([x_cat, x_num], dim=1)
        x = x_num
        batch_size = x.shape[0]
        out = self.fc(x)
        return out

class Seq2Seq(nn.Module):
    def __init__(self, encoder, decoder, device, target_size, embedder=None, mc_dropout=False,
                use_meta_temporal=True):
        super().__init__()

        self.encoder = encoder
        self.decoder = decoder
        self.device = device
        if not torch.cuda.is_available() and self.device is None: 
            self.device = -1
        self.target_size = target_size
        
        self.bayesian = self.decoder.bayesian
        self.mc_dropout = mc_dropout
        self.use_meta_temporal = use_meta_temporal
        
        if embedder is not None:
            self.embedder = embedder
        
        if self.bayesian:
            #Add a learnable rescale factor as in https://openreview.net/pdf?id=CecZ_0t79q
            self.log_rescale_factor = nn.Parameter(torch.ones(1, requires_grad=True))

    def forward(self, src, meta_temporal_input, meta_temporal_target, meta_cat=None, meta_num=None,
               ):
        
        batch_size = src.shape[0]

        if not self.use_meta_temporal:
            meta_temporal_input = None
            meta_temporal_target = None
        
        #print(src)
        #print(meta_temporal_input)
        encoder_outputs, hidden = self.encoder(src, meta_temporal=meta_temporal_input)
        
        embeddings = None
        if hasattr(self, 'embedder') and meta_cat is not None and meta_num is not None:
            embeddings = self.embedder(meta_cat, meta_num).unsqueeze(1)

        # tensor to store decoder outputs
        outputs = torch.zeros(batch_size,
                              self.target_size,
                              self.decoder.output_dim).to(self.device)
        hiddens = torch.zeros(batch_size,
                              self.target_size,
                              self.decoder.dec_hid_dim).to(self.device)
        
        if self.bayesian:
            log_sigmas = torch.zeros(batch_size,
                                     self.target_size,
                                     self.decoder.output_dim).to(self.device)

        inputs = src[:, -1, :].unsqueeze(1)
        
        if self.bayesian:
            inputs = torch.cat([inputs, torch.zeros(*inputs.shape).to(inputs.device)], 2)

        for t in range(0, self.target_size):
            meta_temporal = meta_temporal_target[:, t:t + 1, :] if meta_temporal_target is not None else None
            dec_outputs = self.decoder(inputs, hidden, encoder_outputs, embeddings=embeddings,
                                      meta_temporal=meta_temporal)

            if not self.bayesian:
                output, hidden = dec_outputs
                outputs[:, t:t + 1, :] = output
                hiddens[:, t:t + 1, :] = hidden[-2:-1, :, :].transpose(0, 1)

                inputs = output
            else:
                output, log_sigma, hidden = dec_outputs
                outputs[:, t:t + 1, :] = output
                hiddens[:, t:t + 1, :] = hidden[-2:-1, :, :].transpose(0, 1)
                log_sigmas[:, t:t+1, :] = log_sigma

                inputs = torch.cat([output, log_sigma], dim=2)
        
        #if hasattr(self, 'rescale_factor'):
        #    log_sigmas += 2 * self.rescale_factor

        if not self.bayesian:
            return outputs, hiddens
        else:
            return outputs, log_sigmas, hiddens

def activate_mc_dropout(model):
    for m in model.modules():
        if (type(m) == nn.Dropout) or (type(m) == nn.GRU):
            m.train()

In [18]:
def gen_net(dropout=0.5, bayesian=False, mc_dropout=False, meta_temporal=True):
    embedder = None
    
    if meta_temporal:
        encoder_input_dim = 1 + len(metatemp_columns)
        meta_temporal_dim = len(metatemp_columns)
    else:
        encoder_input_dim = 1
        meta_temporal_dim = 0
        
    encoder = Encoder(input_dim= encoder_input_dim, enc_hid_dim=32, dec_hid_dim=32,
                      num_layers=4, dropout=dropout
                     ).to(device)
    attention = Attention(enc_hid_dim=32, dec_hid_dim=32)
    decoder = Decoder(input_dim=1, output_dim= 1, enc_hid_dim=32, dec_hid_dim=32, fc_dim=32,
                      num_layers=4, dropout=dropout, attention=attention, bayesian=bayesian,
                      embed_dim = None, meta_temporal_dim=meta_temporal_dim
                     ).to(device)
    net = Seq2Seq(encoder, decoder, device, N_output, mc_dropout=mc_dropout, embedder=embedder, use_meta_temporal=meta_temporal).to(device)

    return net

In [ ]:
print(torch.cuda.device_count())  
print(torch.cuda.is_available())   
print(torch.version.cuda) 
nets_lists = {}
#nets_lists['mse_ensembling'] = []
nets_lists['meta_mc_dropout'] = []
for i in range(1):
    net = gen_net(dropout=0.5, bayesian=True, mc_dropout=True, meta_temporal=True)
    train_model(net, loss_type=['fake_baye'], optimizer_parameters=optimizer_parameters,
            epochs=100, eval_every=10)
    nets_lists['meta_mc_dropout'].extend([net]*50)

[x.log_rescale_factor for x in nets_lists['meta_mc_dropout']]

1
True
10.2
